In [0]:
# Imports
from pyspark.sql import functions as F

In [0]:
# Read Bronze customers
df_customers_bronze = spark.table("retail_project.bronze.customers")

In [0]:
display(df_customers_bronze.limit(10))
df_customers_bronze.printSchema()

customer_id tax_id tax_code customer_name state city postcode street number unit region district lon lat ship_to_address valid_from valid_to units_purchased loyalty_segment _bronze_load_ts _bronze_source_path _bronze_file_size _read_timestamp _source_path _file_size 11123757 null null SMITH, SHIRLEY IN BREMEN 46506.0 N CENTER ST 521.0 null Indiana 50.0 -86.1465825 41.4507625 IN, 46506.0, N CENTER ST, 521.0 1532824233 1.548137353E9 34.0 3 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 30585978 null null STEPHENS, GERALDINE M OR ADDRESS 0 NO SITUS null null null null -122.1055158 45.374317 OR, 0, NO SITUS, nan 1523100473 null 18.0 3 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 349822 null null GUZMAN, CARMEN VA VIENNA 22181 HILL RD 2860 null VA null -77.2941261 38.88303270000001 VA, 22181, HILL RD, 2860 1522922493 null 5.0 0 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 27652636 null null HASSETT, PATRICK J WI VILLAGE OF NASHOTAH 53058.0 IVY LANE W333N 5591 null null null -88.40951700000002 43.1213789 WI, 53058.0, IVY LANE, W333N 5591 1531834357 1.558052195E9 7.0 1 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 14437343 null null HENTZ, DIANA L OH COLUMBUS 43228.0 ALLIANCE WAY 5706 null OH FRA -83.158438 39.97821810000001 OH, 43228.0, ALLIANCE WAY, 5706 1517227530 null 0.0 0 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 20441596 null null TIRADO, MARCO A NY Otselic 13072 County Road 16 2792 null NY Chenango -75.7505808 42.7172722 NY, 13072, County Road 16, 2792 1519335250 null 24.0 3 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 5945686 null null SKORA, BRIAN S MI null 48205.0 E 8 MILE RD 16414.0 null null null -82.950874 42.4499233 MI, 48205.0, E 8 MILE RD, 16414.0 1518988242 null 7.0 1 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 5385771 null null SLAWEK, DEAN J PA null 19147-3204 FITZWATER ST 328 null null null -75.14920550000002 39.9389473 PA, 19147-3204, FITZWATER ST, 328 1518239268 null 18.0 3 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 1427940 null null REAVES, LIONEL C VA HOT SPRINGS 24445.0 HOT SPRINGS RD 6419.0 null null null -79.90497859999998 37.8949737 VA, 24445.0, HOT SPRINGS RD, 6419.0 1529087690 null 10.0 2 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361 10457387 null null BONGIOVANNI, KELLY M IN VINCENNES 47591 JERRY ST 2006.0 null Indiana 42.0 -87.519002 38.662178 IN, 47591, JERRY ST, 2006.0 1535887733 null 9.0 2 null null null 2025-12-13T15:38:02.230Z dbfs:/databricks-datasets/retail-org/customers/customers.csv 4550361

root
 |-- customer_id: integer (nullable = true)
 |-- tax_id: double (nullable = true)
 |-- tax_code: string (nullable = true)
 |-- customer_name: string (nullable = true)
 |-- state: string (nullable = true)
 |-- city: string (nullable = true)
 |-- postcode: string (nullable = true)
 |-- street: string (nullable = true)
 |-- number: string (nullable = true)
 |-- unit: string (nullable = true)
 |-- region: string (nullable = true)
 |-- district: string (nullable = true)
 |-- lon: double (nullable = true)
 |-- lat: double (nullable = true)
 |-- ship_to_address: string (nullable = true)
 |-- valid_from: integer (nullable = true)
 |-- valid_to: double (nullable = true)
 |-- units_purchased: double (nullable = true)
 |-- loyalty_segment: integer (nullable = true)
 |-- _bronze_load_ts: timestamp (nullable = true)
 |-- _bronze_source_path: string (nullable = true)
 |-- _bronze_file_size: long (nullable = true)
 |-- _read_timestamp: timestamp (nullable = true)
 |-- _source_path: string (nulla

In [0]:
# validate customer_id
(
    df_customers_bronze
    .groupBy("customer_id")
    .count()
    .orderBy(F.desc("count"))
    .limit(10)
    .display()
)

customer_id count 7237214 2 2388421 2 17286556 2 915104 2 12703248 2 5260201 2 18654833 2 9440771 2 2826093 2 12655486 2

In [0]:
# Discovery check: nulls & data quality
df_customers_bronze.select([
    F.count(F.when(F.col(c).isNull(), c)).alias(c)
    for c in df_customers_bronze.columns
]).display()

customer_id tax_id tax_code customer_name state city postcode street number unit region district lon lat ship_to_address valid_from valid_to units_purchased loyalty_segment _bronze_load_ts _bronze_source_path _bronze_file_size _read_timestamp _source_path _file_size 0 19389 19389 0 0 4765 0 0 123 25613 15152 16732 0 0 0 0 27380 0 0 28813 28813 28813 0 0 0

In [0]:
# Create customer_key as new PK
# customer_key = customer_id + '#' + valid_from
df_customers_with_key = (
    df_customers_bronze
    .withColumn(
        "customer_key",
        F.concat_ws(
            "#",
            F.col("customer_id"),
            F.col("valid_from").cast("string")
        )
    )
)

In [0]:
# df_customers_deduped = df_customers_bronze.dropDuplicates(["customer_id"])


In [0]:
# Silver cleaning & standardization
df_customers_silver = (
    df_customers_with_key
    .select(
        # Added PK: customer_key
        F.col("customer_key").cast("string"),

        F.col("valid_to"),
        F.col("tax_id").cast("string"),
        F.col("tax_code").cast("string"),
        F.col("customer_name").cast("string"),
        F.col("ship_to_address").cast("string"),

        # changed type from double -> int
        F.col("units_purchased").cast("int"),

        F.col("loyalty_segment").cast("string"),

        F.col("customer_id").cast("string"),
        F.col("_read_timestamp").alias("bronze_read_timestamp")
    )
)

In [0]:
# Check product_id uniqueness
df_customers_silver.groupBy("customer_key").count().filter("count > 1").display()


customer_key count

In [0]:
(
    df_customers_silver.write
        .format("delta")
        .mode("overwrite")
        .option("overwriteSchema", "true")
        .saveAsTable("retail_project.silver.customers")
)


In [0]:
spark.table("retail_project.silver.customers").display()


customer_key valid_to tax_id tax_code customer_name ship_to_address units_purchased loyalty_segment customer_id bronze_read_timestamp 11123757#1532824233 1.548137353E9 null null SMITH, SHIRLEY IN, 46506.0, N CENTER ST, 521.0 34 3 11123757 2025-12-13T15:38:02.230Z 30585978#1523100473 null null null STEPHENS, GERALDINE M OR, 0, NO SITUS, nan 18 3 30585978 2025-12-13T15:38:02.230Z 349822#1522922493 null null null GUZMAN, CARMEN VA, 22181, HILL RD, 2860 5 0 349822 2025-12-13T15:38:02.230Z 27652636#1531834357 1.558052195E9 null null HASSETT, PATRICK J WI, 53058.0, IVY LANE, W333N 5591 7 1 27652636 2025-12-13T15:38:02.230Z 14437343#1517227530 null null null HENTZ, DIANA L OH, 43228.0, ALLIANCE WAY, 5706 0 0 14437343 2025-12-13T15:38:02.230Z 20441596#1519335250 null null null TIRADO, MARCO A NY, 13072, County Road 16, 2792 24 3 20441596 2025-12-13T15:38:02.230Z 5945686#1518988242 null null null SKORA, BRIAN S MI, 48205.0, E 8 MILE RD, 16414.0 7 1 5945686 2025-12-13T15:38:02.230Z 5385771#1518239268 null null null SLAWEK, DEAN J PA, 19147-3204, FITZWATER ST, 328 18 3 5385771 2025-12-13T15:38:02.230Z 1427940#1529087690 null null null REAVES, LIONEL C VA, 24445.0, HOT SPRINGS RD, 6419.0 10 2 1427940 2025-12-13T15:38:02.230Z 10457387#1535887733 null null null BONGIOVANNI, KELLY M IN, 47591, JERRY ST, 2006.0 9 2 10457387 2025-12-13T15:38:02.230Z 19154815#1544554334 null null null VERTA, RAYMOND J OH, 44710.0, WERTZ AVE SW, 1224 27 3 19154815 2025-12-13T15:38:02.230Z 2469887#1516971623 null null null BRYANT, KATHRYN I MA, 2382.0, JACOB LANE, 11 7 1 2469887 2025-12-13T15:38:02.230Z 11743397#1529825848 null null null UCZEN, MARK D CA, 95407.0, Gloria Dr, 1473 5 0 11743397 2025-12-13T15:38:02.230Z 9944827#1518955698 null null null HOFFMANN, AARON G IN, 46226, N KITLEY AVE, 4025.0 3 0 9944827 2025-12-13T15:38:02.230Z 11928169#1532887809 null null null OUTTEN, MIA G NJ, 8069.0, Mill Street, 89 6 1 11928169 2025-12-13T15:38:02.230Z 24917207#1537516177 null null null AGUILAR JR, ROBERT FL, 32955.0, CAROLINA AVE, 935 6 1 24917207 2025-12-13T15:38:02.230Z 17211232#1540694264 null null null BALASZEK, LES J CA, 92585, PINE NEEDLE RD, 30090 6 1 17211232 2025-12-13T15:38:02.230Z 7164613#1521504627 null null null BERNARDINO, JAIME GA, 30016, SPRING VALLEY WAY, 170 16 3 7164613 2025-12-13T15:38:02.230Z 23608911#1535788037 null null null KLIMASZEWSKI, GREGORY IL, 61081.0, E 13TH ST, 801 7 1 23608911 2025-12-13T15:38:02.230Z 10603598#1541181492 null null null CRYLEN, TAMMIE NJ, 8243.0, Central Avenue North, 6509 4 0 10603598 2025-12-13T15:38:02.230Z 8858342#1522679974 null null null CLAUDIO, ERIBERTO CA, 96001.0, ORO ST, 4040 6 1 8858342 2025-12-13T15:38:02.230Z 467248#1543078273 null null null MC FADDEN JR, GARDNER E UT, 84123, WEST GERMANIA STREET, 464 8 2 467248 2025-12-13T15:38:02.230Z 5997959#1516018270 null null null KEVIN, SEAN R PA, 18064.0, DANIELS RD, 511 4 0 5997959 2025-12-13T15:38:02.230Z 2581731#1516946202 null null null SCHAFFRATH, STEVEN R MA, 2038.0, MARY ANNE DRIVE, 11 0 0 2581731 2025-12-13T15:38:02.230Z 31920379#1532677354 null null null MAGUIRE, BERNARD J WA, , RESERVOIR, 0.0 2 0 31920379 2025-12-13T15:38:02.230Z 11687899#1528308079 null null null LINTON, JAMES E CA, 95476.0, 3rd St W, 644 3 0 11687899 2025-12-13T15:38:02.230Z 14712172#1531246146 null null null RODGERS, DARLEEN F OH, 43201.0, GIBBARD AVE, 758 3 0 14712172 2025-12-13T15:38:02.230Z 19032398#1528042855 null null null HAILE, ROBERT A NY, 11957, Youngs Road, 1700 1 0 19032398 2025-12-13T15:38:02.230Z 16355000#1530098698 null null null VAZQUEZ, KEYLA OH, 43228, WESTBROOK VILLAGE DR, 1830 9 2 16355000 2025-12-13T15:38:02.230Z 10549224#1521481144 null null null DWYER, THOMAS H NJ, 8251.0, East Atlantic Avenue, 48 5 0 10549224 2025-12-13T15:38:02.230Z 25390741#1516606956 null null null STUBBS SR, LAWRENCE D WI, 53220, S 83RD ST, 3649.0 2 0 25390741 2025-12-13T15:38:02.230Z 9722000#1521882767 null null null POLLEY, BARBARA E NJ, 7405.0, LAKESIDE TRL, 6 10 2 9722000 2025-12-13T15: